# Query database

Notebook for running Python sqlite3 commands for querying database.

Specific code blocks run separately to produce statistics.

Not intended to be run all in one session, search or scroll to find targeted SQL commands.

## Setup

In [1]:
import matplotlib.pyplot as plt
import numpy as np

In [2]:
import sqlite3
import re
import json
import os

In [27]:
# db_path = os.path.expanduser("~/data/db/arxiv_db_images.sqlite3")
db_path = os.path.expanduser("~/data/db/arxiv_db_images_600k.sqlite3")

In [28]:
# Here we import the sqlite3 database and create a cursor

db = sqlite3.connect(db_path)
c = db.cursor()

## Testing

Get the pragma table info for each table

In [29]:
c.execute('PRAGMA TABLE_INFO({})'.format("metadata"))
info = c.fetchall()

print("\nColumn Info:\nID, Name, Type, NotNull, DefaultVal, PrimaryKey")
for col in info:
    print(col)


Column Info:
ID, Name, Type, NotNull, DefaultVal, PrimaryKey
(0, 'id', 'INTEGER', 0, None, 1)
(1, 'identifier', 'TEXT', 0, None, 0)
(2, 'created', 'TEXT', 0, None, 0)
(3, 'cat', 'TEXT', 0, None, 0)
(4, 'authors', 'TEXT', 0, None, 0)
(5, 'title', 'TEXT', 0, None, 0)
(6, 'abstract', 'TEXT', 0, None, 0)
(7, 'licence', 'TEXT', 0, None, 0)


In [30]:
c.execute('PRAGMA TABLE_INFO({})'.format("images"))
info = c.fetchall()

print("\nColumn Info:\nID, Name, Type, NotNull, DefaultVal, PrimaryKey")
for col in info:
    print(col)


Column Info:
ID, Name, Type, NotNull, DefaultVal, PrimaryKey
(0, 'id', 'INTEGER', 0, None, 1)
(1, 'identifier', 'TEXT', 0, None, 0)
(2, 'filename', 'TEXT', 0, None, 0)
(3, 'filesize', 'INT', 0, None, 0)
(4, 'path', 'TEXT', 0, None, 0)
(5, 'x', 'INT', 0, None, 0)
(6, 'y', 'INT', 0, None, 0)
(7, 'imageformat', 'TEXT', 0, None, 0)
(8, 'creator', 'TEXT', 0, None, 0)
(9, 'vggpred', 'TEXT', 0, None, 0)
(10, 'caption', 'INTEGER', 0, None, 0)


Quick test to retrive one row

In [ ]:
c.execute('''
    SELECT * 
    FROM images 
    ORDER BY ROWID ASC 
    LIMIT 1
''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
c.execute('''
    SELECT * 
    FROM metadata 
    ORDER BY ROWID ASC 
    LIMIT 1
''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
c.execute('''
    SELECT * 
    FROM captions 
    ORDER BY ROWID ASC 
    LIMIT 2
''')
rows = c.fetchall()
for row in rows:
    print(row)

## Writing to org mode

This function takes a list of tuples from an SQL query and writes this data into an org table with pipes and dashes.

In [ ]:
def write_to_org(data, _write_file):
    with open(_write_file, "w+") as write_file:
        for row in data:
            print("|", file=write_file, end = '')
            for item in row:
                print(str(item).replace("\n", " "), file=write_file, end = '')
                print("|", file=write_file, end = '')
            print("\n", file=write_file, end = '')
        write_file.close()

## Get samples from each table

Find a few random entries from both metadata and images, write to org mode

In [ ]:
cursor = c.execute('''
    SELECT * 
    FROM metadata 
    ORDER BY RANDOM() 
    LIMIT 3
''')
rows = c.fetchall()
headings = [description[0] for description in cursor.description]
rows.insert(0, headings)

write_to_org(rows, "metadata_samples.org")

In [ ]:
cursor = c.execute('''
    SELECT * 
    FROM images 
    ORDER BY RANDOM() 
    LIMIT 3
''')
rows = c.fetchall()
headings = [description[0] for description in cursor.description]
rows.insert(0, headings)

write_to_org(rows, "images_samples.org")

In [ ]:
cursor = c.execute('''
    SELECT * 
    FROM captions 
    ORDER BY RANDOM() 
    LIMIT 3
''')
rows = c.fetchall()
headings = [description[0] for description in cursor.description]
rows.insert(0, headings)

write_to_org(rows, "captions_samples.org")

## Find duplicate entries

In [ ]:
# look for duplicate rows in the metadata table
c.execute('''
    SELECT identifier, COUNT(identifier)
    FROM metadata
    GROUP BY identifier
    HAVING COUNT(identifier) > 1
    ''')
rows = c.fetchall()
for row in rows:
    print(row)
    
duplicates = rows

sql = ('''
    SELECT id, identifier, created, cat, authors, title
    FROM metadata
    WHERE identifier IS ?
''')

for d in duplicates[:]:
    c.execute(sql, (d[0], ))
    rows = c.fetchall()
    
    same = True
    r1 = rows[0][1:]
    for row in rows[1:]:
        if r1 != row[1:]:
            same = False
    if same is False:
        print("-----",d[0])
        for row in rows:
            print(row)
        print("----- !!! mismatch !!! -----")
#     else:
#         print("*** entry identitical ***")

print(f'total number of duplicate entries: {len(rows)}')

In [ ]:
# look for duplicate rows in the images table
# this brings up totals for images by article ID
c.execute('''
    SELECT identifier, COUNT(identifier)
    FROM images
    GROUP BY identifier
    HAVING COUNT(identifier) > 0
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# look for duplicate images (search by filename, filesize, and identifier)
# there is quite a lot of these, but that is how the source data was uploaded
c.execute('''
    SELECT identifier, filename, filesize, path, COUNT(*) c
    FROM images
    GROUP BY identifier, filename, filesize
    HAVING c > 1
    ''')
rows = c.fetchall()
for row in rows:
    print(row)
print(f'total number of duplicate images: {len(rows)}')

## Database queries for statistics

### Earliest dates

In [ ]:
# Find the earliest date of an article

c.execute('''
    SELECT created, identifier
    FROM metadata
    WHERE created IS NOT NULL
    ORDER BY created ASC
    LIMIT 20
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find the earliest dated articles and get the associated images

c.execute('''
    SELECT images.id, metadata.created, metadata.identifier 
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE metadata.created IS NOT NULL
    ORDER BY created ASC
    LIMIT 40
    ''')
    
rows = c.fetchall()
for row in rows:
    print(row)

### Total numbers of articles and images

In [ ]:
# Find total number of rows in metadata

c.execute('''
    SELECT count(*)
    FROM metadata
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find total number of rows in images

c.execute('''
    SELECT count(*)
    FROM images
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find total number of rows in images 
# (filtering out images without size or imageformat)

c.execute('''
    SELECT count(*)
    FROM images
    WHERE x IS NOT null AND x != ''
    AND y IS NOT null AND y != ''
    AND imageformat is not null AND imageformat != ''
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

### Average image sizes

In [ ]:
# Get average of the x size column

c.execute('''
    SELECT avg(x)
    FROM images
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get average of the y size column

c.execute('''
    SELECT avg(y)
    FROM images
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get median of the x size column

c.execute('''
    SELECT x
    FROM images
    ORDER by x
    LIMIT 1
    OFFSET (SELECT COUNT(*) FROM images) / 2
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get median of the y size column

c.execute('''
    SELECT y
    FROM images
    ORDER by y
    LIMIT 1
    OFFSET (SELECT COUNT(*) FROM images) / 2
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

### Missing fields

In [ ]:
# Find where there are NULL values for x

c.execute('''
    SELECT id, identifier, path, filename, filesize, x, y, imageformat
    FROM images
    WHERE x is null or x = ''
    OR y is null or y = ''
    OR imageformat is null or imageformat = ''
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
print(len(rows))

In [ ]:
# generate a text file listing paths of files that couldn't be identified
with open("identify_errors_db.txt", "a+") as f:
    for row in rows[:]:
        filepath = row[2][1:] + "/" + row[3]
        print(str(row[0]) + "," + filepath)
        f.write(str(row[0]) + "," + filepath + "\n")

In [ ]:
# Find where there are NULL values for y

c.execute('''
    SELECT id, identifier, path, filename, filesize, x, y, imageformat
    FROM images
    WHERE y is null or y = ''
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
print(len(rows))

In [ ]:
# Find where there are NULL values for identifier

c.execute('''
    SELECT id, identifier, path, filesize, x, y, imageformat
    FROM images
    WHERE identifier is null or identifier = ''
    ''')
rows = c.fetchall()
for row in rows:
    print(row)
print(f'total number of entries found: {len(rows)}')
# no result is a good result!

In [ ]:
# Find where there are NULL values for filesize

c.execute('''
    SELECT id, identifier, path, filesize, x, y, imageformat
    FROM images
    WHERE filesize is null or filesize = ''
    ''')
rows = c.fetchall()
for row in rows:
    print(row)
print(f'total number of entries found: {len(rows)}')

In [ ]:
# Get number of articles with no category
# this seems to give no results

c.execute('''
    SELECT identifier, cat
    FROM metadata
    WHERE cat IS NULL OR cat = '' OR cat = 'None'
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find where there is no matching metadata for a given image

c.execute('''
    SELECT count(images.identifier), images.identifier
    FROM images
    LEFT JOIN metadata ON metadata.identifier = images.identifier
    WHERE metadata.identifier IS NULL
    GROUP BY images.identifier
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

### Averages of images

In [ ]:
# Get total number of images per article

c.execute('''
    SELECT images.identifier, metadata.cat, count(images.identifier)    
    FROM images 
    LEFT JOIN metadata ON images.identifier = metadata.identifier 
    GROUP BY images.identifier
    ORDER BY count(images.identifier)
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get total number of images per category

c.execute('''
    SELECT metadata.cat, count(images.identifier)
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier 
    GROUP BY metadata.cat
    ORDER BY count(images.identifier) DESC    
    LIMIT 200
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get total number of images per primary category only

c.execute('''
    SELECT substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1), count(images.identifier)
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier 
    GROUP BY substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1)
    ORDER BY count(images.identifier) DESC    
    ''')
rows = c.fetchall()
for row in rows:
    print(row)
write_to_org(rows, "stats_images_by_category.org")

In [ ]:
# Get total number of images per primary category only - with a specific filter

c.execute('''
    SELECT substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1) c, count(images.identifier)
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE c = "cond-mat.mes-hall"
    GROUP BY c
    ORDER BY count(images.identifier) DESC    
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find total number of images in a given category and year

c.execute('''
    SELECT substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1) c, 
            count(images.identifier), 
            strftime("%Y", metadata.created) as 'Y'
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE c = "cs.CV"
    AND Y = '2019'
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get total number of images per primary category with multiple filters

c.execute('''
    SELECT substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1) c, count(images.identifier)
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE c = "cs.LG"
    OR c = "cs.CV"
    OR c = "stat.ML"
    OR c = "cs.AI"
    GROUP BY c
    ORDER BY count(images.identifier) DESC    
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get total number of images per primary category

c.execute('''
    SELECT substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1), count(images.identifier)
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    GROUP BY substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1)
    ORDER BY count(images.identifier) DESC    
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
for row in rows:
    print(str(row[1]) + " \t " + str(row[0]))

### Totals by month/year

In [ ]:
# Find number of articles by year

c.execute('''
    SELECT count(metadata.identifier), strftime("%Y", metadata.created) as 'Y'
    FROM metadata
    GROUP BY strftime("%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find number of articles in each month/year

c.execute('''
    SELECT count(metadata.identifier), strftime("%m-%Y", metadata.created) as 'mY'
    FROM metadata
    GROUP BY strftime("%m-%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find number of images by year

c.execute('''
    SELECT count(images.identifier), strftime("%Y", metadata.created) as 'Y'
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier 
    GROUP BY strftime("%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find number of images in each month/year

c.execute('''
    SELECT count(images.identifier), strftime("%m-%Y", metadata.created) as 'mY'
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier 
    GROUP BY strftime("%m-%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
total = 0
for row in rows:
    total += row[0]
print(total)

#### ...and by category

In [ ]:
# Find number of articles by year by category - cs.CV

c.execute('''
    SELECT count(metadata.identifier), strftime("%Y", metadata.created) as 'Y'
    FROM metadata
    WHERE substr(trim(cat),1,instr(trim(cat)||' ',' ')-1) = 'cs.CV'
    GROUP BY strftime("%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find number of articles by year by category, for a specific query

c.execute('''
    SELECT count(metadata.identifier), strftime("%Y", metadata.created) as 'Y'
    FROM metadata
    WHERE substr(trim(cat),1,instr(trim(cat)||' ',' ')-1) = 'cs.CV'
    AND strftime("%Y", metadata.created) = '2018'
    GROUP BY strftime("%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find number of articles by year by category, for a specific query

c.execute('''
    SELECT count(metadata.identifier), strftime("%Y", metadata.created) as 'Y'
    FROM metadata
    WHERE substr(trim(cat),1,instr(trim(cat)||' ',' ')-1) = 'cs.CV'
    AND strftime("%Y", metadata.created) = '2012'
    GROUP BY strftime("%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

### Other metadata

In [ ]:
# Find number of images per each different imageformat

c.execute('''
    SELECT imageformat, count(imageformat)
    FROM images
    GROUP BY imageformat
    ORDER BY count(imageformat) DESC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get only the first listed category

c.execute('''
    SELECT identifier, cat, substr(trim(cat),1,instr(trim(cat)||' ',' ')-1)
    FROM metadata
    LIMIT 20
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get the licence information for number of articles

c.execute('''
    SELECT licence, COUNT(licence)
    FROM metadata
    GROUP BY licence
    HAVING COUNT(identifier) > 0
    ''')
rows = c.fetchall()
for row in rows:
    print(row)
write_to_org(rows, "licences.org")

In [ ]:
# Get the number of images per licence

c.execute('''
    SELECT metadata.licence, COUNT(metadata.licence)
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    GROUP BY metadata.licence
    HAVING COUNT(images.identifier) > 0
    ORDER BY COUNT(metadata.licence)
    ''')
rows = c.fetchall()
for row in rows:
    print(row)
write_to_org(rows, "image_licences.org")

In [ ]:
# Get number of articles for each primary category

c.execute('''
    SELECT count(substr(trim(cat),1,instr(trim(cat)||' ',' ')-1)) AS cnt, substr(trim(cat),1,instr(trim(cat)||' ',' ')-1)
    FROM metadata
    GROUP BY substr(trim(cat),1,instr(trim(cat)||' ',' ')-1)
    ORDER BY cnt DESC
    ''')
rows = c.fetchall()
for row in rows:
    print(str(row[0]) + " \t" + row[1])

### Querying by image extension

In [ ]:
# define reverse function
db.create_function("reverse", 1, lambda s: s[::-1])

In [ ]:
# Get the number of images per extension
# DON'T filter based on X or Y dimension

c.execute('''
    SELECT COUNT(reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1))), reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)) AS extension
    FROM images
    GROUP BY extension 
    ''')

rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get the number of images per extension
# filter based on X or Y dimension

c.execute('''
    SELECT COUNT(reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1))), reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)) AS extension
    FROM images
    WHERE x is not null and x != ''
    AND y is not null and y != ''
    AND imageformat is not null and imageformat != ''
    GROUP BY extension
    ''')

rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get the number of images per extension by year
# filter based on X or Y dimension
# 2018 only

c.execute('''
    SELECT reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)) AS extension, COUNT(reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)))
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE x is not null and x != ''
    AND y is not null and y != ''
    AND imageformat is not null and imageformat != ''
    AND strftime("%Y", metadata.created) = '2018'
    GROUP BY extension
    ''')

rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get the number of images per extension with percentages
# filter based on X or Y dimension

c.execute('''
    SELECT reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)) AS extension, COUNT(reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)))
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE x is not null and x != ''
    AND y is not null and y != ''
    AND imageformat is not null and imageformat != ''
    GROUP BY extension
    ''')

rows = c.fetchall()
    
total = 0
for row in rows:
    total += row[1]
print("total:", total)

print("*" * 20)

alldata = []
for i, row in enumerate(rows):
    alldata.append([row[0], row[1], row[1]/total])
for d in alldata:
    print("{} | {} | {:2.2%}".format(d[0], d[1], d[2]))

### Get extensions by years and get statistics for changing percentages

This section is quite a convoluted way of finding the number of images by extension for each year and then calculating the change over time for these. Requires running a number of iterative searches.

In [ ]:
# Get list of years
years = []

c.execute('''
    SELECT strftime("%Y", metadata.created), COUNT(strftime("%Y", metadata.created))
    FROM metadata
    GROUP BY strftime("%Y", metadata.created)
    ''')

rows = c.fetchall()
for row in rows:
    print(row)
    years.append(row[0])
print(years)

In [ ]:
# Get the number of images per extension by year
# filter based on X or Y dimension

data = []

# manually selecting years
# years = ["2000", "2005", "2010", "2015"]

db.create_function("reverse", 1, lambda s: s[::-1])
sql = ('''
    SELECT reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)) AS extension, COUNT(reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)))
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE x is not null and x != ''
    AND y is not null and y != ''
    AND imageformat is not null and imageformat != ''
    AND strftime("%Y", metadata.created) = ?
    GROUP BY extension
    ''')

# data = []

for y, year in enumerate(years):
    print("*" * 20)
    print(year)
    print("*" * 20)
    c.execute(sql, (year, ))

    rows = c.fetchall()
#     for row in rows:
#         print(row)
    total = 0
    for row in rows:
        total += row[1]
    print("total:", total)

    data = []
    for i, row in enumerate(rows):
        data.append([row[0], row[1], row[1]/total])
    for d in data:
        print("{} | {} | {:2.2%}".format(d[0], d[1], d[2]))
#     print(data)

In [ ]:
for d in data:
    print(d)

In [ ]:
# get proportion as percentage

total = 0
for row in rows:
    total += row[1]
print(total)

data = []
for row in rows:
    data.append([row[0], row[1], row[1]/total])
print(data)

In [ ]:
# take second element for sort
def takeSecond(elem):
    return elem[1]
data.sort(key=takeSecond)

for d in data:
    print("{} | {} | {:2.2%}".format(d[0], d[1], d[2]))

In [ ]:
values = []
names = []
for row in rows:
    values.append(row[0])
    names.append(row[1])

In [ ]:
values_save = values
names_save = names

In [ ]:
for i, name in enumerate(names.copy()):
    names[i] = name.lower()
print(names)

In [ ]:
print(values)
print(names)
print(len(values))
print(len(names))

In [ ]:
total = 0
for row in rows:
    total += row[0]
print(total)

In [ ]:
write_to_org(rows, "stats_articles_by_cat.org")
# print("* number of articles by category", file=write_file)

### Image metadata

Here we pull the 'creator' field from the table, with some cleaning using regex. There are two versions, one without the year, and one with years. The version without years creates an ordered and summed list of all image creator fields. The version with years pulls all the creator data and then builds an ordered table for creator fields by year.

Note: code is a little sketchy, use with discretion.

In [31]:
get_year = False
# get_year = True

In [32]:
# Get the number of images per creator

if get_year is False:
    c.execute('''
        SELECT images.creator, COUNT(images.creator)
        FROM images
        GROUP BY images.creator
        ORDER BY COUNT(images.creator) DESC
        ''')
else:
    c.execute('''
        SELECT images.creator, COUNT(images.creator), strftime("%Y", metadata.created)
        FROM images
        LEFT JOIN metadata ON images.identifier = metadata.identifier 
        GROUP BY images.creator, strftime("%Y", metadata.created)
        ORDER BY images.creator ASC
        ''')
rows = c.fetchall()
print(len(rows))
print(rows[:20])

28418
[('-', 137591), ('TeX', 14018), ('SM', 13037), ('OriginLab Corporation', 8876), ('GIMP PostScript file plugin V 1.17 by Peter Kirchgessner', 7094), ('R', 6703), ('MATLAB, The Mathworks, Inc.', 6326), ('Mathematica', 6016), ('MATLAB, The MathWorks, Inc.', 5846), ('ImageMagick', 4596), ('jpeg2ps V1.9 by Thomas Merz', 3545), ('fig2dev Version 3.2 Patchlevel 4', 3479), ('PGPLOT', 3343), ('cairo 1.10.2 (http://cairographics.org)', 3248), ('gnuplot 4.0 patchlevel 0', 3126), ('Grace-5.1.22', 3080), ('PGPLOT [PSDRIV 6.6]', 2841), ('PScript5.dll Version 5.2.2', 2767), ('matplotlib 1.5.1, http://matplotlib.org', 2763), ('cairo 1.14.6 (http://cairographics.org)', 2618)]


In [33]:
# remove the ® symbol
creators = []

if get_year is False:
    for i, (creator, count) in enumerate(rows):
        if "®" in creator:
            print("found symbol")
            print(creator)
            new_creator = creator.replace("®", "")
            print(new_creator)
            creators.append([new_creator, count])
        else:
            creators.append([creator, count])
else:
    for i, (creator, count, year) in enumerate(rows):
        if "®" in creator:
            print("found symbol")
            print(creator)
            new_creator = creator.replace("®", "")
            print(new_creator)
            creators.append([new_creator, count, year])
        else:
            creators.append([creator, count, year])
print(creators[:10])

found symbol
Microsoft® PowerPoint® 2013
Microsoft PowerPoint 2013
found symbol
Microsoft® PowerPoint® 2016
Microsoft PowerPoint 2016
found symbol
Microsoft® PowerPoint® 2010
Microsoft PowerPoint 2010
found symbol
Microsoft® Visio® 2013
Microsoft Visio 2013
found symbol
Microsoft® Visio® 2010
Microsoft Visio 2010
found symbol
Microsoft® Visio® 2016
Microsoft Visio 2016
found symbol
Microsoft® Office PowerPoint® 2007
Microsoft Office PowerPoint 2007
found symbol
Microsoft® Office Visio® 2007
Microsoft Office Visio 2007
found symbol
Microsoft® Word 2010
Microsoft Word 2010
found symbol
Microsoft® Excel® 2013
Microsoft Excel 2013
found symbol
Microsoft® Office Word 2007
Microsoft Office Word 2007
found symbol
Microsoft® Word 2013
Microsoft Word 2013
found symbol
Microsoft® Word 2016
Microsoft Word 2016
found symbol
Microsoft® Excel® 2010
Microsoft Excel 2010
found symbol
Microsoft® Excel® 2016
Microsoft Excel 2016
found symbol
Microsoft® PowerPoint® for Office 365
Microsoft PowerPoint for

In [34]:
cleaned = []

regex = r'\n?\s?(?:http://|www.|edited with|created with the |esp|afpl|windows|adobe|gpl\s|apple|wolfram|gnu\s|microsoft office |microsoft|the\s|version|v\.|v\s)?\s?((?:[\w\/]+(?:[\-]?(?!\d)))+)(?:\sversion|v\.|v\ |\,|\n|\s|\-|\.|\(|\))?\s?'

if get_year is False:
    for creator, total in creators[:]:
        print(creator + " | " + str(total))
        match = re.search(regex, creator, re.IGNORECASE)
        if match:
            cleaned.append([match.group(1), total])
            print(">>>",match.group(1))
        else:
            cleaned.append([creator, total])
else:
    for creator, total, year in creators[:]:
        print(f'{creator} | {total} | {year}')
        match = re.search(regex, creator, re.IGNORECASE)
        if match:
            cleaned.append([match.group(1), total, year])
            print(">>>",match.group(1))
        else:
            cleaned.append([creator, total, year])
            
for row in cleaned[50:100]:
    print(row)

- | 137591
TeX | 14018
>>> TeX
SM | 13037
>>> SM
OriginLab Corporation | 8876
>>> OriginLab
GIMP PostScript file plugin V 1.17 by Peter Kirchgessner | 7094
>>> GIMP
R | 6703
>>> R
MATLAB, The Mathworks, Inc. | 6326
>>> MATLAB
Mathematica | 6016
>>> Mathematica
MATLAB, The MathWorks, Inc. | 5846
>>> MATLAB
ImageMagick | 4596
>>> ImageMagick
jpeg2ps V1.9 by Thomas Merz | 3545
>>> jpeg2ps
fig2dev Version 3.2 Patchlevel 4 | 3479
>>> fig2dev
PGPLOT | 3343
>>> PGPLOT
cairo 1.10.2 (http://cairographics.org) | 3248
>>> cairo
gnuplot 4.0 patchlevel 0 | 3126
>>> gnuplot
Grace-5.1.22 | 3080
>>> Grace
PGPLOT [PSDRIV 6.6] | 2841
>>> PGPLOT
PScript5.dll Version 5.2.2 | 2767
>>> PScript5
matplotlib 1.5.1, http://matplotlib.org | 2763
>>> matplotlib
cairo 1.14.6 (http://cairographics.org) | 2618
>>> cairo
cairo 1.12.16 (http://cairographics.org) | 2611
>>> cairo
 | 2578
matplotlib 2.2.2, http://matplotlib.org | 2543
>>> matplotlib
matplotlib 2.0.2, http://matplotlib.org | 2513
>>> matplotlib
R Softwar

IDL Version 6.0, Compaq Tru64 (OSF alpha m64) | 25
>>> IDL
ImageMagick 6.5.7 | 25
>>> ImageMagick
Ipe 7.1.3 | 25
>>> Ipe
MATLAB, The MathWorks, Inc. Version 8.0.0.783 (R2012b). Operating System: Darwin 12.3.0 Darwin Kernel Version 12.3.0: Sun Jan  6 22:37:10 PST 2013; root:xnu-2050.22.13~1/RELEASE_X86_64 x86_64. | 25
>>> MATLAB
MATLAB, The MathWorks, Inc. Version 8.0.0.783 (R2012b). Operating System: Linux 2.6.32-358.el6.x86_64 #1 SMP Fri Feb 22 00:31:26 UTC 2013 x86_64. | 25
>>> MATLAB
MATLAB, The MathWorks, Inc. Version 8.0.0.783 (R2012b). Operating System: Microsoft Windows Server 2008 R2. | 25
>>> MATLAB
MATLAB, The MathWorks, Inc. Version 8.1.0.604 (R2013a). Operating System: Linux 3.2.0-45-generic #70-Ubuntu SMP Wed May 29 20:12:06 UTC 2013 x86_64. | 25
>>> MATLAB
MATLAB, The Mathworks, Inc. Version 7.10.0.499 (R2010a). Operating System: Darwin 11.4.2 Darwin Kernel Version 11.4.2: Thu Aug 23 16:25:48 PDT 2012; root:xnu-1699.32.7~1/RELEASE_X86_64 x86_64. | 25
>>> MATLAB
MATLAB, Th

KaleidaGraph: LaserWriter 8 J1-8.6 | 7
>>> KaleidaGraph
KaleidaGraph: LaserWriter 8 J1-8.6.5 | 7
>>> KaleidaGraph
KaleidaGraph: LaserWriter 8 Z1-8.7.1 | 7
>>> KaleidaGraph
LEXPSNT3 Version 7.4 | 7
>>> LEXPSNT3
LaTeX with hyperref package and class compositionalityarticle 2018/07/22 v1 class for Compositionality - The open-access journal for the mathematics of composition (http://www.compositionality-journal.org) | 7
>>> LaTeX
Luca | 7
>>> Luca
MATLAB, The MathWorks, Inc. Version 7.11.0.584 (R2010b). Operating System: Linux 2.6.38-8-generic #42-Ubuntu SMP Mon Apr 11 03:31:24 UTC 2011 x86_64. | 7
>>> MATLAB
MATLAB, The MathWorks, Inc. Version 7.12.0.635 (R2011a). Operating System: Darwin 11.4.2 Darwin Kernel Version 11.4.2: Wed May 30 20:13:51 PDT 2012; root:xnu-1699.31.2~1/RELEASE_X86_64 x86_64. | 7
>>> MATLAB
MATLAB, The MathWorks, Inc. Version 7.12.0.635 (R2011a). Operating System: Darwin 13.2.0 Darwin Kernel Version 13.2.0: Thu Apr 17 23:03:13 PDT 2014; root:xnu-2422.100.13~1/RELEASE

>>> PDFCreator
PDFescape Desktop | 4
>>> PDFescape
PDFsharp 1.31.1789-g (www.pdfsharp.com) | 4
>>> PDFsharp
PLplot Version 5.9.6 | 4
>>> PLplot
Pakey | 4
>>> Pakey
Pau Rabassa,,, | 4
>>> Pau
Peter Nemeth | 4
>>> Peter
PhotoImpact Ver6.0 | 4
>>> PhotoImpact
Photos 1.5 | 4
>>> Photos
Photoshop Version 2.5.1b15 | 4
>>> Photoshop
Physics | 4
>>> Physics
Pixelmator 3.6 | 4
>>> Pixelmator
Podgląd | 4
>>> Podgląd
PostScript PDriver module 4.41 | 4
>>> PostScript
Produced by GNUPLOT 5.2 patchlevel 7 | 4
>>> Produced
PyX 0.13 | 4
>>> PyX
Qin Zhou | 4
>>> Qin
Qt 4.6.2 | 4
>>> Qt
QuarkXPress(R) 8.0 | 4
>>> QuarkXPress
RAL GKS 1.37 Sun - Workstation 2722 | 4
>>> RAL
RAL GKS 1.37-1 x86_64-unknown-linux-gnu - Workstation 2703 | 4
>>> RAL
ROOT Version 5.17/08 | 4
>>> ROOT
ROOT Version 5.18/00d | 4
>>> ROOT
ROOT Version 5.19/03 | 4
>>> ROOT
ROOT Version 5.21/04 | 4
>>> ROOT
ROOT Version 5.22/00f | 4
>>> ROOT
ROOT Version 5.32/00-rc1 | 4
>>> ROOT
ROOT Version 6.05/01 | 4
>>> ROOT
ROOT Version 6.09/03 |

>>> guy
hamann | 3
>>> hamann
hamid | 3
>>> hamid
haque | 3
>>> haque
hartwig | 3
>>> hartwig
harut | 3
>>> harut
hasee | 3
>>> hasee
hawthorn@hawthorn.math.waikato.ac.nz (Ian Hawthorn) | 3
>>> hawthorn
hayakawa | 3
>>> hayakawa
hc@starbase.mp.qub.ac.uk, | 3
>>> hc
hcj | 3
>>> hcj
hd_fq127 | 3
>>> hd_fq127
hdiamant | 3
>>> hdiamant
henry | 3
>>> henry
hetet | 3
>>> hetet
hhamedivafa | 3
>>> hhamedivafa
high@sptoir.uchicago.edu, /home/high | 3
>>> high
hiramatsu | 3
>>> hiramatsu
hirota | 3
>>> hirota
hirotani | 3
>>> hirotani
hke | 3
>>> hke
hlamm | 3
>>> hlamm
homePC | 3
>>> homePC
honecker | 3
>>> honecker
honma@cmsvt2.u-aizu.ac.jp with xmgr | 3
>>> honma
horbach | 3
>>> horbach
hrtankova | 3
>>> hrtankova
http://github.com/softdevteam/warmup_experiment | 3
>>> github
hui | 3
>>> hui
hurier@mic-hurier.ias.u-psud.fr, /Users/hurier | 3
>>> hurier
hxw | 3
>>> hxw
hyejung hyejung | 3
>>> hyejung
hyoshino | 3
>>> hyoshino
i@LENOVO-4FC1E742 \(U-LENOVO-4FC1E742\\i,S-1-5-21-1728873906-229612

...

>>> adriano
adwait | 1
>>> adwait
ady | 1
>>> ady
aeberurs | 1
>>> aeberurs
aernst@perseus.ari.uni-heidelberg.de, /home/Tux/aernst/def-dc-And | 1
>>> aernst
af | 1
>>> af
afansjev@Afanasjev with xmgr | 1
>>> afansjev
afansjev@afanasjev.phys.nd.edu with xmgr | 1
>>> afansjev
afarres | 1
>>> afarres
afeldmei@ma014630.ads.eso.org, /Users/afeldmei/cluster/5286/jeans | 1
>>> afeldmei
afeldmei@ma014630.ads.eso.org, /Users/afeldmei/cluster/5286/phot/SB | 1
>>> afeldmei
afeldmei@ma017793.ads.eso.org, /Users/afeldmei/KMOS/starkit/prog | 1
>>> afeldmei
afowler | 1
>>> afowler
afuhrer with JaxoDraw-2.0-0 | 1
>>> afuhrer
aga@andrey with xmgr | 1
>>> aga
agallagher@uhppc55.herts.ac.uk, | 1
>>> agallagher
agallagher@virgo, /home/agallagher/CEMP/Programs/gband_p1_plots | 1
>>> agallagher
agarcia@Antonios-MacBook-Pro-2, /Users/agarcia/PUFFY/ANALYSIS | 1
>>> agarcia
agarcia@Antonios-MacBook-Pro-2.local, /Users/agarcia/PiMenc/ANALYSIS | 1
>>> agarcia
agarcia@unknownACBC3285C43F, /Users/agarcia/PUFFY/ANA

>>> dph3es
dph3rw | 1
>>> dph3rw
dpoilbla@pcipt715.unil.ch with xmgr | 1
>>> dpoilbla
dpontin@host116-247.eng.dundee.ac.uk, /Users/dpontin/Desktop/mixing | 1
>>> dpontin
dr2kim@linux, /home/dr2kim | 1
>>> dr2kim
dragon123 | 1
>>> dragon123
dragozzi@neptune, /home/dragozzi/research/multitrans/tbpexop | 1
>>> dragozzi
drake3@NegraModelo, /home/drake3/test_decorr/HAT20 | 1
>>> drake3
drake3@NegraModelo, /home/drake3/test_decorr/WASP8 | 1
>>> drake3
drathlev | 1
>>> drathlev
dream | 1
>>> dream
dreese@tycho00, /home/dreese/sendme | 1
>>> dreese
dreizler@astro58, /home/astro58/dreizler/PROG/mercury6/KOIs/TEST | 1
>>> dreizler
driebel@bigred-bluejay, /home/driebel | 1
>>> driebel
drocklin | 1
>>> drocklin
droenner | 1
>>> droenner
droniou@localhost \(Droniou Jerome,,,\) | 1
>>> droniou
drosch | 1
>>> drosch
drossel@a26 with xmgr | 1
>>> drossel
drossi | 1
>>> drossi
drostest | 1
>>> drostest
drozdovskaya@mare.strw.leidenuniv.nl, | 1
>>> drozdovskaya
drupke@feanor.local, /Users/drupke/src/idl

>>> jpeg2ps
jpeg2ps V1.3 by Thomas Merz | 1
>>> jpeg2ps
jpeng@jcnp2 with xmgr | 1
>>> jpeng
jperaud | 1
>>> jperaud
jpg2ps V1.0 by Christoph Schulte | 1
>>> jpg2ps
jphuang@axp40.phy.cuhk.edu.hk with xmgr | 1
>>> jphuang
jpineda@dhcp152-74.cfa.harvard.edu, | 1
>>> jpineda
jplowman@ithilien.int.colorado.edu, /data/jplowman/GONG_Simulator | 1
>>> jplowman
jplowman@ithilien.int.colorado.edu, /data/jplowman/Simple_DEM_code | 1
>>> jplowman
jpmor | 1
>>> jpmor
jponnela | 1
>>> jponnela
jppalao@aphrodite.fh.huji.ac.il with xmgr | 1
>>> jppalao
jps2ps version 0.07c, 5 septembre 2004 | 1
>>> jps2ps
jpurcell@somf203.math.ias.edu (Jessica Purcell) | 1
>>> jpurcell
jr | 1
>>> jr
jracusin@gs66-kochab, /Users/jracusin/GRBs | 1
>>> jracusin
jracusin@wcne-128-154-209-204.gsfc.nasa.gov, | 1
>>> jracusin
jrad@ame.astro.washington.edu, | 1
>>> jrad
jrad@ame.astro.washington.edu, /astro/users/jrad/research/wise | 1
>>> jrad
jramasco | 1
>>> jramasco
jramirez | 1
>>> jramirez
jrathbor@acrux | 1
>>> jrathbo

nperra | 1
>>> nperra
npetrov@linux54 with xmgr | 1
>>> npetrov
nrc25@tcm34.phy.cam.ac.uk with xmgr | 1
>>> nrc25
nrezaei | 1
>>> nrezaei
nrjf | 1
>>> nrjf
nsas | 1
>>> nsas
nsm10nsm10 nsm10 | 1
>>> nsm10nsm10
ntakashi@takashi.riken.go.jp with xmgr | 1
>>> ntakashi
ntr@theo01, /ptmp/mpia/ntr/GBI/relax/testruns/tau_diff_30-2 | 1
>>> ntr
ntr@theo02, /ptmp/mpia/ntr/GBI/relax/05_10_576 | 1
>>> ntr
nucave | 1
>>> nucave
nuclear | 1
>>> nuclear
nud001@ii122056.klientdrift.uib.no \(Saket Saurabh\) | 1
>>> nud001
nue with JaxoDraw-1.3-1 | 1
>>> nue
nunes@lithium with xmgr | 1
>>> nunes
nuno@borboleta.dfis.uevora.pt with xmgr | 1
>>> nuno
nunocruz | 1
>>> nunocruz
nuria alvarez crespo | 1
>>> nuria
nuriav@Obelix.local, | 1
>>> nuriav
nuriav@Obelix.local, /Users/nuriav/Work/Particules/MILICH/TAULES | 1
>>> nuriav
nurur@brahma.astro.umd.edu, | 1
>>> nurur
nvidia | 1
>>> nvidia
nw@MN11434.local (Nathalie Wahl) | 1
>>> nw
nw@Nathalies-MacBook-Air.local (Nathalie Wahl) | 1
>>> nw
nwt2de@Rosat.astro.

sub253 | 1
>>> sub253
subhadeep | 1
>>> subhadeep
subhamoy@pegasus.iiap.res.in, /home/subhamoy/idlfiles | 1
>>> subhamoy
subhasis@alix.lkb.ens.fr with xmgr | 1
>>> subhasis
subodh | 1
>>> subodh
subrata | 1
>>> subrata
suchismita | 1
>>> suchismita
sudden with JaxoDraw-1.3-2 | 1
>>> sudden
sudhanva | 1
>>> sudhanva
sudip@localhost.localdomain, /home/sudip/Videos | 1
>>> sudip
sudipto | 1
>>> sudipto
sudou@blade with xmgr | 1
>>> sudou
suematsu@csuematu.hep.s.kanazawa-u.ac.jp with xmgr | 1
>>> suematsu
sueshige | 1
>>> sueshige
suhail | 1
>>> suhail
sui@cuphyc with xmgr | 1
>>> sui
sule1 | 1
>>> sule1
sullivanm@asosx10.physics.ox.ac.uk, | 1
>>> sullivanm
suman samui | 1
>>> suman
sumei | 1
>>> sumei
summers@scotty with xmgr | 1
>>> summers
sun yuyi | 1
>>> sun
sun1:kari(Kari Rummukainen) | 1
>>> sun1
sungho | 1
>>> sungho
sungwoo | 1
>>> sungwoo
sunhao | 1
>>> sunhao
sunqf@balin with xmgr | 1
>>> sunqf
sunta@p0xxx with xmgr | 1
>>> sunta
sunting | 1
>>> sunting
sunxiaoqi | 1
>>> sunxiao

In [35]:
if get_year is False:
    filename = "creator_cleaned.json"
else:
    filename = "creator_cleaned_years.json"

In [36]:
with open(filename, 'w') as outfile:
    json.dump(cleaned, outfile)

In [37]:
def sum_duplicates(a, ind):
    length = len(a)
    print("length:",length)
    
    if ind == length:
        print("ind == length")
        print("ending!")
        return 1    
    else:
        target = a[ind][0]
        print("target:",target)

        for i, (creator, total) in enumerate(a):
            removables = []
            if i != ind:
#                 print("i != ind")
#                 print("i:",i,"ind:",ind)
                if creator == target:
                    print("creator == target")
                    print("creator",creator,"target",target)
                    removables.append(i)
#             else:
                # if i and ind are the same, don't compare
#                 print("i == ind")
#                 print("i:",i,"ind:",ind)
        print("removables:",removables)
        for rem in removables:
            a[ind][1] += a[rem][1]
            del a[rem]
        return 0

In [39]:
# sum up totals
# create new array with each entry

with open(filename) as infile:
    full_list = json.load(infile)
    
summed = cleaned[:]

ind = 0
running = True
while running:
    length = len(summed)
    print("length:",length)
    
    if ind == length:
        print("ind == length")
        print("--- ending! ---")
        running = False # stop if at the end of the list   
    else:
        target = summed[ind][0]
        print("target:",target)
        removables = []
        if get_year is False:
            for i, (creator, total) in enumerate(summed):
                if i != ind:
                    if creator.lower() == target.lower():
                        print("i:", i, "creator",creator,"target",target)
                        removables.append(i)
        else:
            for i, (creator, total, year) in enumerate(summed):
                if i != ind:
                    if creator.lower() == target.lower() and year == summed[ind][2]:
                        print("i:", i, "creator:",creator,"target:",target,"year:",year)
                        removables.append(i)     

        print("removables:",removables)

        for rem in removables[::-1]:
            print("removing item", rem)
            summed[ind][1] += summed[rem][1]
            del summed[rem]
        ind += 1

length: 28418
target: -
removables: []
length: 28418
target: TeX
i: 7229 creator TeX target TeX
i: 7230 creator TeX target TeX
i: 9402 creator TeX target TeX
i: 11610 creator TeX target TeX
i: 11611 creator TeX target TeX
i: 11612 creator TeX target TeX
i: 11613 creator TeX target TeX
i: 11614 creator TeX target TeX
i: 11615 creator TeX target TeX
i: 11616 creator TeX target TeX
i: 11617 creator TeX target TeX
i: 11618 creator TeX target TeX
i: 11619 creator TeX target TeX
i: 11620 creator TeX target TeX
i: 11621 creator TeX target TeX
i: 11622 creator TeX target TeX
i: 11623 creator TeX target TeX
i: 11624 creator TeX target TeX
i: 11625 creator TeX target TeX
i: 11626 creator TeX target TeX
i: 11627 creator TeX target TeX
i: 11628 creator TeX target TeX
i: 11629 creator TeX target TeX
i: 11630 creator TeX target TeX
i: 11631 creator TeX target TeX
i: 11632 creator TeX target TeX
i: 11633 creator TeX target TeX
i: 11634 creator TeX target TeX
i: 11635 creator TeX target TeX
i: 11636 c

i: 1773 creator MATLAB target MATLAB
i: 1774 creator MATLAB target MATLAB
i: 1775 creator MATLAB target MATLAB
i: 1793 creator MATLAB target MATLAB
i: 1810 creator MATLAB target MATLAB
i: 1811 creator MATLAB target MATLAB
i: 1812 creator MATLAB target MATLAB
i: 1813 creator MATLAB target MATLAB
i: 1814 creator MATLAB target MATLAB
i: 1815 creator MATLAB target MATLAB
i: 1816 creator MATLAB target MATLAB
i: 1817 creator MATLAB target MATLAB
i: 1818 creator MATLAB target MATLAB
i: 1843 creator MATLAB target MATLAB
i: 1844 creator MATLAB target MATLAB
i: 1865 creator MATLAB target MATLAB
i: 1866 creator MATLAB target MATLAB
i: 1867 creator MATLAB target MATLAB
i: 1868 creator MATLAB target MATLAB
i: 1869 creator MATLAB target MATLAB
i: 1870 creator MATLAB target MATLAB
i: 1871 creator MATLAB target MATLAB
i: 1872 creator MATLAB target MATLAB
i: 1873 creator MATLAB target MATLAB
i: 1874 creator MATLAB target MATLAB
i: 1875 creator MATLAB target MATLAB
i: 1876 creator MATLAB target MATLAB
i

i: 3141 creator MATLAB target MATLAB
i: 3142 creator MATLAB target MATLAB
i: 3143 creator MATLAB target MATLAB
i: 3144 creator MATLAB target MATLAB
i: 3145 creator MATLAB target MATLAB
i: 3146 creator MATLAB target MATLAB
i: 3147 creator MATLAB target MATLAB
i: 3148 creator MATLAB target MATLAB
i: 3149 creator MATLAB target MATLAB
i: 3150 creator MATLAB target MATLAB
i: 3151 creator MATLAB target MATLAB
i: 3152 creator MATLAB target MATLAB
i: 3153 creator MATLAB target MATLAB
i: 3313 creator MATLAB target MATLAB
i: 3314 creator MATLAB target MATLAB
i: 3315 creator MATLAB target MATLAB
i: 3439 creator MATLAB target MATLAB
i: 3440 creator MATLAB target MATLAB
i: 3441 creator MATLAB target MATLAB
i: 3442 creator MATLAB target MATLAB
i: 3443 creator MATLAB target MATLAB
i: 3444 creator MATLAB target MATLAB
i: 3445 creator MATLAB target MATLAB
i: 3446 creator MATLAB target MATLAB
i: 3447 creator MATLAB target MATLAB
i: 3448 creator MATLAB target MATLAB
i: 3449 creator MATLAB target MATLAB
i

i: 5821 creator MATLAB target MATLAB
i: 5822 creator MATLAB target MATLAB
i: 5823 creator MATLAB target MATLAB
i: 5824 creator MATLAB target MATLAB
i: 5825 creator MATLAB target MATLAB
i: 5826 creator MATLAB target MATLAB
i: 5827 creator MATLAB target MATLAB
i: 5828 creator MATLAB target MATLAB
i: 5829 creator MATLAB target MATLAB
i: 5830 creator MATLAB target MATLAB
i: 5831 creator MATLAB target MATLAB
i: 5832 creator MATLAB target MATLAB
i: 5833 creator MATLAB target MATLAB
i: 5834 creator MATLAB target MATLAB
i: 5835 creator MATLAB target MATLAB
i: 5836 creator MATLAB target MATLAB
i: 5837 creator MATLAB target MATLAB
i: 5838 creator MATLAB target MATLAB
i: 5839 creator MATLAB target MATLAB
i: 5840 creator MATLAB target MATLAB
i: 5841 creator MATLAB target MATLAB
i: 5842 creator MATLAB target MATLAB
i: 5843 creator MATLAB target MATLAB
i: 5844 creator MATLAB target MATLAB
i: 5845 creator MATLAB target MATLAB
i: 5846 creator MATLAB target MATLAB
i: 5847 creator MATLAB target MATLAB
i

i: 7222 creator MATLAB target MATLAB
i: 7223 creator MATLAB target MATLAB
i: 7224 creator MATLAB target MATLAB
i: 7225 creator MATLAB target MATLAB
i: 7226 creator MATLAB target MATLAB
i: 7227 creator MATLAB target MATLAB
i: 7228 creator MATLAB target MATLAB
i: 7229 creator MATLAB target MATLAB
i: 7230 creator MATLAB target MATLAB
i: 7231 creator MATLAB target MATLAB
i: 7232 creator MATLAB target MATLAB
i: 7233 creator MATLAB target MATLAB
i: 7234 creator MATLAB target MATLAB
i: 7235 creator MATLAB target MATLAB
i: 7236 creator MATLAB target MATLAB
i: 7237 creator MATLAB target MATLAB
i: 7238 creator MATLAB target MATLAB
i: 7239 creator MATLAB target MATLAB
i: 7240 creator MATLAB target MATLAB
i: 7241 creator MATLAB target MATLAB
i: 8104 creator MATLAB target MATLAB
i: 8105 creator MATLAB target MATLAB
i: 8106 creator MATLAB target MATLAB
i: 8107 creator MATLAB target MATLAB
i: 8108 creator MATLAB target MATLAB
i: 8109 creator MATLAB target MATLAB
i: 8110 creator MATLAB target MATLAB
i

...

removables: []
length: 12700
target: tcli
i: 11673 creator tcli target tcli
i: 11674 creator tcli target tcli
removables: [11673, 11674]
removing item 11674
removing item 11673
length: 12698
target: tcrawfor
removables: []
length: 12698
target: team_king55
removables: []
length: 12698
target: teboul
removables: []
length: 12698
target: teet
removables: []
length: 12698
target: teilab
i: 11678 creator teilab target teilab
removables: [11678]
removing item 11678
length: 12697
target: tejedor
removables: []
length: 12697
target: tek2ps
removables: []
length: 12697
target: telnov
removables: []
length: 12697
target: teppich
removables: []
length: 12697
target: terak
removables: []
length: 12697
target: teramura
removables: []
length: 12697
target: tere
removables: []
length: 12697
target: terese
removables: []
length: 12697
target: teresiteresi
removables: []
length: 12697
target: tero
removables: []
length: 12697
target: terra
removables: []
length: 12697
target: tess
removables: []
lengt

length: 12683
target: veberic
removables: []
length: 12683
target: veen
removables: []
length: 12683
target: vekhter
removables: []
length: 12683
target: velenik
removables: []
length: 12683
target: vennin
removables: []
length: 12683
target: ventura
removables: []
length: 12683
target: venu
removables: []
length: 12683
target: vero
removables: []
length: 12683
target: verzicco
removables: []
length: 12683
target: veselov
removables: []
length: 12683
target: vgrechka
removables: []
length: 12683
target: vguzey
removables: []
length: 12683
target: viard
removables: []
length: 12683
target: vicente
removables: []
length: 12683
target: vichi
removables: []
length: 12683
target: vicini
removables: []
length: 12683
target: victorleblanc
removables: []
length: 12683
target: vieiro
removables: []
length: 12683
target: viel
removables: []
length: 12683
target: vijetasingh
removables: []
length: 12683
target: villain
removables: []
length: 12683
target: ville
removables: []
length: 12683
target

removables: []
length: 12664
target: wuxudong
removables: []
length: 12664
target: wvanroos
removables: []
length: 12664
target: wwalasik
removables: []
length: 12664
target: freepdfconvert
removables: []
length: 12664
target: un
removables: []
length: 12664
target: wxw
removables: []
length: 12664
target: wyang
removables: []
length: 12664
target: wyd
removables: []
length: 12664
target: wyf
removables: []
length: 12664
target: wyfwenwen
removables: []
length: 12664
target: wyong
removables: []
length: 12664
target: wyz
removables: []
length: 12664
target: wzdammy
removables: []
length: 12664
target: wzgold
removables: []
length: 12664
target: wzz
removables: []
length: 12664
target: x_yunli
removables: []
length: 12664
target: xabier
removables: []
length: 12664
target: xbany
removables: []
length: 12664
target: xbauch
removables: []
length: 12664
target: xcui
removables: []
length: 12664
target: xcwang
removables: []
length: 12664
target: xenon
removables: []
length: 12664
target: x

removables: []
length: 12649
target: ywong
removables: []
length: 12649
target: yxz
removables: []
length: 12649
target: yy510
removables: []
length: 12649
target: yyang
i: 12290 creator yyang target yyang
removables: [12290]
removing item 12290
length: 12648
target: yyaoag
removables: []
length: 12648
target: yys
removables: []
length: 12648
target: yzchou
removables: []
length: 12648
target: yzhang
removables: []
length: 12648
target: yzz0115
removables: []
length: 12648
target: yzzhang
removables: []
length: 12648
target: z00424156
removables: []
length: 12648
target: z3119608
removables: []
length: 12648
target: z3213007
removables: []
length: 12648
target: z3297688
removables: []
length: 12648
target: z5094476
removables: []
length: 12648
target: zahrasad
removables: []
length: 12648
target: zaigao
removables: []
length: 12648
target: zamora
removables: []
length: 12648
target: zanetted
removables: []
length: 12648
target: zang
removables: []
length: 12648
target: zaninett
removab

target: 崔国歆
removables: []
length: 12637
target: 廖
removables: []
length: 12637
target: 张
i: 12501 creator 张 target 张
removables: [12501]
removing item 12501
length: 12636
target: 张zk
removables: []
length: 12636
target: 张华宇
removables: []
length: 12636
target: 张含望
removables: []
length: 12636
target: 张家俊
removables: []
length: 12636
target: 张珊
removables: []
length: 12636
target: 徐昊
removables: []
length: 12636
target: 徐炜鸿
removables: []
length: 12636
target: 恺
removables: []
length: 12636
target: 敏捷蔡
removables: []
length: 12636
target: 文凯
removables: []
length: 12636
target: 斎藤
removables: []
length: 12636
target: 於
removables: []
length: 12636
target: 昌浩
removables: []
length: 12636
target: 明珠
removables: []
length: 12636
target: 易
removables: []
length: 12636
target: 春伟
removables: []
length: 12636
target: 晋东
removables: []
length: 12636
target: 曹若菡
removables: []
length: 12636
target: 有宝
removables: []
length: 12636
target: 朱
i: 12521 creator 朱 target 朱
removables: [12521]
removi

In [40]:
# print results
print(len(summed))
for row in summed:
    print(row)

12631
['-', 137591]
['TeX', 14330]
['SM', 13157]
['OriginLab', 8876]
['GIMP', 14366]
['R', 11687]
['MATLAB', 95290]
['Mathematica', 49196]
['ImageMagick', 8050]
['jpeg2ps', 4851]
['fig2dev', 29881]
['PGPLOT', 9175]
['cairo', 42486]
['gnuplot', 37288]
['Grace', 20276]
['PScript5', 4641]
['matplotlib', 91527]
['', 2578]
['Keynote', 3272]
['LaTeX', 2682]
['Illustrator', 26938]
['inkscape', 2947]
['PowerPoint', 5339]
['dvips', 21988]
['Preview', 1705]
['FreeHEP', 1283]
['HIGZ', 12747]
['CorelDRAW', 8283]
['PSCRIPT', 2218]
['gnome-screenshot', 1058]
['Wolfram', 1401]
['xmgr', 2778]
['TECPLOT', 916]
['Acrobat', 7109]
['Unknown', 1305]
['Draw', 856]
['Unified', 1079]
['XV', 3659]
['IDL', 38367]
['fko', 811]
['ImageReady', 755]
['Sun', 767]
['Maple', 777]
['Office', 707]
['Ipe', 4675]
['pdfresizer', 630]
['Chromium', 597]
['Tk', 595]
['Ghostscript', 19823]
['dvipsk', 1125]
['pnmtops', 532]
['Mathematica-PSRender', 511]
['ROOT', 27784]
['IgorPro', 501]
['EPS-conv', 592]
['TRIUMF', 460]
['AIPS',

['Samsung', 2]
['Sangseung', 2]
['Sara', 6]
['Sasha', 8]
['Saurav', 4]
['Schwen', 4]
['Scott', 14]
['Segun', 6]
['Sengupta', 2]
['Sensor', 2]
['Seo', 2]
['Seongah', 2]
['Seonghoon', 2]
['Seunghyun', 6]
['Seymur', 2]
['Shahrouz', 2]
['Shannon', 2]
['Shaohe', 2]
['Shi-Xiong', 2]
['Shibata', 2]
['Shich', 2]
['Shingo', 4]
['ShingoMotoki', 2]
['Shuinai', 2]
['Shuming', 4]
['Shuo', 2]
['ShuvPink', 6]
['Shuyang', 6]
['Sibelius', 2]
['Siggi', 2]
['Sijie', 2]
['Sikander', 2]
['Simona', 8]
['Simone', 6]
['SimpleText', 2]
['Simulator', 2]
['Siu', 2]
['Sivaraman', 2]
['Skim', 2]
['SlidePlayer', 2]
['Smolders', 2]
['Softinterface', 2]
['Sofya', 2]
['Soheil', 2]
['Solo', 2]
['Song', 12]
['Songlin', 4]
['Songrui', 2]
['Sorin', 4]
['Spectra', 2]
['Stanislav', 4]
['Stefanie', 4]
['Stella', 8]
['Stephane', 4]
['Stephen', 24]
['Stuart', 4]
['Sudeep', 2]
['Sumedha', 4]
['Sumiran', 4]
['Sune', 2]
['Supriyo', 4]
['Sushovan', 6]
['Sylvester', 2]
['Symeon', 2]
['TING', 6]
['TJLee', 2]
['TS', 2]
['TStanev', 2]

['Diaz', 3]
['Dick', 1]
['Didier', 5]
['Diederick', 1]
['Diederik', 1]
['Diestel', 1]
['Dima', 5]
['Dimitri', 3]
['Dimitrios', 3]
['Dimoklis', 1]
['Dinesh', 1]
['Dinh', 1]
['Diniz', 3]
['Diogo', 1]
['Dionysis', 1]
['Dipak', 1]
['Dipanjan', 1]
['Diptarama', 1]
['Division', 1]
['Dmitrii', 1]
['Dmitry', 9]
['Dmytro', 5]
['Dobromir', 1]
['Dominik', 1]
['Dominique', 1]
['DonQuixote', 1]
['Donald', 1]
['DongWen', 1]
['Doro', 1]
['Dovydas', 1]
['DrFent', 1]
['DraftSight', 1]
['Dragana', 1]
['Drake', 1]
['Drawboard', 1]
['DreamTale', 1]
['Dreams', 1]
['Dropbox', 1]
['Du', 1]
['DuFanXin', 1]
['Ducoin', 1]
['Duine', 1]
['Duits', 1]
['Dung', 1]
['Durga', 1]
['DxO', 1]
['Département', 1]
['E1130H-ylu50', 1]
['EAGLE', 1]
['EECS', 1]
['EFicke', 1]
['EGO', 1]
['EGSLAB6', 1]
['EJG', 1]
['EJUST', 1]
['ENSiLeung', 1]
['EP3', 1]
['EPSTool', 1]
['ESRlab', 1]
['ESTAVROU', 1]
['EZPLOT', 1]
['Earl', 1]
['Ed', 1]
['EdGraph', 1]
['Eden', 1]
['Edison', 1]
['Editor', 1]
['Edwin', 1]
['Egor', 1]
['Eike', 1]
['Eji

['bolind', 1]
['bom', 1]
['bonanos', 1]
['bonati', 1]
['bonca', 1]
['bondaren', 1]
['bonfand', 1]
['bongjae', 1]
['boni', 1]
['bonito', 1]
['borda', 1]
['borgnino', 1]
['borgonov', 1]
['bottero', 1]
['botvinn', 1]
['bouchetj', 1]
['boue', 1]
['boulven', 1]
['bourdin', 1]
['bousso', 1]
['bowles', 1]
['box', 1]
['bpbowler', 1]
['bps', 1]
['bqs', 1]
['br', 1]
['brafax', 1]
['bramakko', 1]
['brandenb', 3]
['brandt', 1]
['bratati', 1]
['brausche', 1]
['breitsma', 1]
['brenig', 1]
['brennema', 1]
['brettsalmon', 1]
['brezzi', 1]
['briansullivan', 1]
['briant', 1]
['brick', 1]
['brij', 1]
['brinks', 1]
['brinzani', 1]
['brisaboa', 1]
['brito', 3]
['brt', 1]
['brtka', 1]
['bruegman', 1]
['brunato', 1]
['brune', 1]
['bruni', 1]
['bruun', 1]
['brv10492', 1]
['bryk', 1]
['bsch63', 1]
['bseguin', 1]
['bsitarski', 1]
['bszafran', 1]
['btamas', 1]
['btingley', 1]
['buballa', 1]
['budefu', 1]
['bugaev', 1]
['bungaro', 1]
['bunker', 1]
['buptlvlab', 1]
['burcin', 5]
['burcu', 1]
['burns', 5]
['burrell

['mim', 1]
['mine', 1]
['minezaki', 1]
['ming_cheng', 1]
['mingo', 1]
['mingzheg', 1]
['minoshim', 3]
['minye', 1]
['mipl', 1]
['miptuom', 1]
['mira', 1]
['miranda', 3]
['mireille', 1]
['mirfan', 1]
['mirko', 3]
['miro', 1]
['miroslav2', 1]
['mirza', 1]
['mischler', 1]
['mishaq01', 1]
['mishchenko', 1]
['mishka', 1]
['misho', 1]
['mithun', 1]
['mithuno', 1]
['mitter', 1]
['miyake', 1]
['miyoshi', 1]
['miyoungko', 1]
['mizuno', 1]
['mizuta', 1]
['mjanvier', 1]
['mjc63', 1]
['mjg', 1]
['mjimenez', 1]
['mjki2mb2', 1]
['mjm', 1]
['mjohnson', 1]
['mjthoraval', 1]
['mjw209', 1]
['mkbbox', 23]
['mkilbing', 1]
['mkinza', 1]
['mkirch', 1]
['mkirk', 1]
['mklatt', 1]
['mklein', 3]
['mkluge', 1]
['mkoga', 1]
['mkokubo', 1]
['mkounkel', 5]
['ml5197', 1]
['mlampis', 1]
['mlb', 1]
['mlee2', 1]
['mliu', 1]
['mlorke', 1]
['mlw105', 1]
['mm', 1]
['mm2f11', 1]
['mmacdonald', 1]
['mmachace', 1]
['mmarina', 1]
['mmarines', 1]
['mmarzl', 1]
['mmattern', 1]
['mmezcua', 1]
['mmhassani', 1]
['mmin', 1]
['mmitc

In [41]:
if get_year is False:
    summed_filename = "creator_summed.json"
else:
    summed_filename = "creator_summed_years.json"

In [42]:
with open(summed_filename, 'w') as outfile:
    json.dump(summed, outfile)

In [43]:
with open(summed_filename, 'r') as infile:
    summed = json.load(infile)
    
sorted_list = sorted(summed, key=lambda x: x[1], reverse=True)
print(sorted_list[:20])

list_of_creators = []
for row in sorted_list:
    list_of_creators.append(row[0])
    
print(list_of_creators)

[['-', 137591], ['MATLAB', 95290], ['matplotlib', 91527], ['Mathematica', 49196], ['cairo', 42486], ['IDL', 38367], ['gnuplot', 37288], ['fig2dev', 29881], ['ROOT', 27784], ['Illustrator', 26938], ['dvips', 21988], ['Grace', 20276], ['Ghostscript', 19823], ['GIMP', 14366], ['TeX', 14330], ['SM', 13157], ['HIGZ', 12747], ['R', 11687], ['PGPLOT', 9175], ['OriginLab', 8876]]
['-', 'MATLAB', 'matplotlib', 'Mathematica', 'cairo', 'IDL', 'gnuplot', 'fig2dev', 'ROOT', 'Illustrator', 'dvips', 'Grace', 'Ghostscript', 'GIMP', 'TeX', 'SM', 'HIGZ', 'R', 'PGPLOT', 'OriginLab', 'Photoshop', 'CorelDRAW', 'ImageMagick', 'Acrobat', 'PowerPoint', 'jpeg2ps', 'Ipe', 'PScript5', 'XV', 'OmniGraffle', 'Keynote', 'inkscape', 'xmgr', 'LaTeX', '', 'GraphicConverter', 'PSCRIPT', 'GTVIRT', 'Preview', 'Wolfram', 'Visio', 'Tgif', 'Unknown', 'FreeHEP', 'ACE/gr', 'Ipelib', 'KaleidaGraph', 'dvipsk', 'Unified', 'gnome-screenshot', 'Veusz', 'TECPLOT', 'Draw', 'fko', 'LibreOffice', 'Canvas', 'Maple', 'Sun', 'ImageReady',

In [23]:
write_to_org(sorted_list, "creator_totals_summed_sorted.org")

NameError: name 'write_to_org' is not defined

In [ ]:
if get_year is True:
    ordered_creator_list = []

    # take the top 100 creators from the sorted list
    for c, n in sorted_list[:100]:
        creator_sublist = []
        # work by year
        for yy in reversed(range(1990, 2019)):
    #         print(yy, c)
        #     print(c, n)
            added = False
            for row in summed:
                if c.lower() == row[0].lower() and str(yy) == row[2]:
                    creator_sublist.append(row)
                    added = True
            if added == False:
                creator_sublist.append([c, 0, yy])
    #     print(creator_sublist)
        ordered_creator_list.append(creator_sublist)
    
    for i in range(len(ordered_creator_list)):
        ordered_creator_list[i][2] = str(ordered_creator_list[i][2])
    
    for r in ordered_creator_list[:3]:
        print(r)

In [ ]:
if get_year is True:
    with open("creator_totals_all_years_test.org", "w+") as write_file:
        # first row
        print("| creator |", file=write_file, end = '')
        for yy in reversed(range(1990, 2019)):
            print(str(yy), file=write_file, end = '')
            print("|", file=write_file, end = '')
        print("\n", file=write_file, end = '')

        for row in ordered_creator_list:
            print("row:", row)
            print("| ", file=write_file, end = '')
            print(str(row[0][0]).replace("\n", " "), file=write_file, end = '')
            print("|", file=write_file, end = '')
        #     print(row)
            for yy in reversed(range(1990, 2019)):
                for item in row:
    #                 print("item:", item)
    #                 print("yy:", yy)
                    if item[2] == str(yy) or item[2] == yy or str(item[2]) == str(yy):
                        print(">>> match:", item)
                        print(item[1], file=write_file, end = '')
                        print("|", file=write_file, end = '')
            print("\n", file=write_file, end = '')
    write_file.close()

### Number of images per licence

In [ ]:
# Get the number of images per creator -- use a search term for creator

c.execute('''
    SELECT images.creator, COUNT(images.creator)
    FROM images
    WHERE images.creator LIKE 'matlab%' COLLATE NOCASE
    GROUP BY images.creator
    ORDER BY COUNT(images.creator) DESC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
total = 0
for name, num in rows:
    total += num
print(total)

In [ ]:
print("|-|-|-|")
for row in rows[1:16]:
    per = str(round((row[1]/10053059*100), 2))
    print("|" + per + "|" + str(row[1]) + "|" + row[0] + '|')
print("|-|-|-|")

### Get image paths for 2019/2020

SQLite query joining tables and finding images of that year, formatted for other scripts in text file that has `filepath,id`

In [ ]:
c.execute('''
    SELECT images.id, images.path, images.filename, strftime("%Y", metadata.created) as "Y"
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier 
    WHERE strftime("%Y", metadata.created) = '2019'
    OR strftime("%Y", metadata.created) = '2020'
    ''')
rows = c.fetchall()
print(len(rows))
for row in rows:
    print(row)

In [ ]:
# write to file

writepath = os.path.expanduser("~/data/paths/paths_src_update_sqlite.txt")
    
with open(writepath, "w+") as write_file:
    for id_num, path, filename, year in rows[:]:
        line = "{}/{},{}".format(path, filename, id_num)
    #     print(line)
        print(line, file=write_file, end = '\n')

### Get numbers of images for given years and categories

In [ ]:
# Find number of images by year by category, for a specific query (cs.LG)

c.execute('''
    SELECT count(images.identifier), strftime("%Y", metadata.created) as 'Y'
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE substr(trim(cat),1,instr(trim(cat)||' ',' ')-1) = 'cs.LG'
    GROUP BY strftime("%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
total = 0
for row in rows:
    print(row)
    total += row[0]
print(f'total number of images: {total}')

In [ ]:
# Find number of images by year by category, for a specific query

c.execute('''
    SELECT count(images.identifier), strftime("%Y", metadata.created) as 'Y'
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    GROUP BY strftime("%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
total = 0
for row in rows:
    print(row)
    total += row[0]
print(f'total number of images: {total}')

#### sanity check for number of papers in a given category and timeframe

In [ ]:
sql = ("SELECT metadata.cat, metadata.id "
    "FROM metadata "
    "WHERE metadata.created BETWEEN date('2012-01-01') "
    "AND date('2012-12-31') "
    "AND substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1) = ?")

c.execute(sql, ("cs.AI", ))
rows = c.fetchall()

print(len(rows))

In [ ]:
sql = '''SELECT licence, count(licence)
    FROM metadata
    GROUP BY licence'''

c.execute(sql, )
rows = c.fetchall()

print(len(rows))

#### Grab predictions

Format for JavaScript

In [ ]:
sql = '''SELECT substr(trim(vggpred),1,instr(trim(vggpred)||' ',' ')-1) as p, 
                count(substr(trim(vggpred),1,instr(trim(vggpred)||' ',' ')-1))
        FROM images
        GROUP BY p
        ORDER BY count(p) DESC'''

In [ ]:
sql = '''SELECT substr(trim(authors),1,instr(trim(authors)||' ',',')-1) as p, 
                count(substr(trim(authors),1,instr(trim(authors)||' ',',')-1))
        FROM metadata
        GROUP BY p
        ORDER BY count(p) DESC'''

In [5]:
sql = '''SELECT substr(trim(creator),1,instr(trim(creator)||' ',',')-1) as p, 
                count(substr(trim(creator),1,instr(trim(creator)||' ',',')-1))
        FROM images
        GROUP BY p
        ORDER BY count(p) DESC'''

In [6]:
c.execute(sql, )
rows = c.fetchall()

print(len(rows))

12410


In [7]:
for i, row in enumerate(rows[1:539]):
    print(i, row)

0 ('MATLAB', 895795)
1 ('(MATLAB', 179334)
2 ('matplotlib 1.5.1', 60494)
3 ('matplotlib 2.0.2', 55073)
4 ('matplotlib 2.2.2', 54556)
5 ('matplotlib 1.3.1', 52293)
6 ('matplotlib version 2.2.2', 37771)
7 ('matplotlib 2.2.3', 37748)
8 ('GIMP PostScript file plugin V 1', 36501)
9 ('matplotlib 3.0.3', 34769)
10 ('matplotlib 3.1.1', 34155)
11 ('matplotlib 2.0.0', 33136)
12 ('matplotlib 1.4.3', 30907)
13 ('matplotlib 3.0.2', 30051)
14 ('matplotlib 1.5.3', 26517)
15 ('matplotlib version 3.0.3', 25168)
16 ('matplotlib 2.1.0', 24823)
17 ('matplotlib 2.1.2', 23118)
18 ('matplotlib version 2.2.3', 21797)
19 ('matplotlib version 3.0.2', 20461)
20 ('IDL Version 7.0', 20318)
21 ('matplotlib version3.1.1', 19697)
22 ('Sun Microsystems', 16851)
23 ('matplotlib version 2.1.2', 16157)
24 ('matplotlib version 1.3.1', 16001)
25 ('matplotlib 3.1.0', 15415)
26 ('matplotlib version 2.1.0', 14910)
27 ('matplotlib version 1.5.1', 12847)
28 ('matplotlib 1.4.2', 12680)
29 ('matplotlib 2.1.1', 12412)
30 ('IDL Ver

In [9]:
data = {}
data['options'] = []
for row in rows[:500]:
    data['options'].append({
        'cat': str(row[0]),
        'label': str(row[1])
    })
print(data)

{'options': [{'cat': '', 'label': '9944146'}, {'cat': 'MATLAB', 'label': '895795'}, {'cat': '(MATLAB', 'label': '179334'}, {'cat': 'matplotlib 1.5.1', 'label': '60494'}, {'cat': 'matplotlib 2.0.2', 'label': '55073'}, {'cat': 'matplotlib 2.2.2', 'label': '54556'}, {'cat': 'matplotlib 1.3.1', 'label': '52293'}, {'cat': 'matplotlib version 2.2.2', 'label': '37771'}, {'cat': 'matplotlib 2.2.3', 'label': '37748'}, {'cat': 'GIMP PostScript file plugin V 1', 'label': '36501'}, {'cat': 'matplotlib 3.0.3', 'label': '34769'}, {'cat': 'matplotlib 3.1.1', 'label': '34155'}, {'cat': 'matplotlib 2.0.0', 'label': '33136'}, {'cat': 'matplotlib 1.4.3', 'label': '30907'}, {'cat': 'matplotlib 3.0.2', 'label': '30051'}, {'cat': 'matplotlib 1.5.3', 'label': '26517'}, {'cat': 'matplotlib version 3.0.3', 'label': '25168'}, {'cat': 'matplotlib 2.1.0', 'label': '24823'}, {'cat': 'matplotlib 2.1.2', 'label': '23118'}, {'cat': 'matplotlib version 2.2.3', 'label': '21797'}, {'cat': 'matplotlib version 3.0.2', 'la

In [ ]:
len(summed)

To get the formatted creator field, run the queries from above including cleaning and summing, then use the summed list to print JSON

In [46]:
data = {}
data['options'] = []
for row in sorted_list[:200]:
    data['options'].append({
        'cat': str(row[0]),
        'label': str(row[1])
    })
print(data)

{'options': [{'cat': '-', 'label': '137591'}, {'cat': 'MATLAB', 'label': '95290'}, {'cat': 'matplotlib', 'label': '91527'}, {'cat': 'Mathematica', 'label': '49196'}, {'cat': 'cairo', 'label': '42486'}, {'cat': 'IDL', 'label': '38367'}, {'cat': 'gnuplot', 'label': '37288'}, {'cat': 'fig2dev', 'label': '29881'}, {'cat': 'ROOT', 'label': '27784'}, {'cat': 'Illustrator', 'label': '26938'}, {'cat': 'dvips', 'label': '21988'}, {'cat': 'Grace', 'label': '20276'}, {'cat': 'Ghostscript', 'label': '19823'}, {'cat': 'GIMP', 'label': '14366'}, {'cat': 'TeX', 'label': '14330'}, {'cat': 'SM', 'label': '13157'}, {'cat': 'HIGZ', 'label': '12747'}, {'cat': 'R', 'label': '11687'}, {'cat': 'PGPLOT', 'label': '9175'}, {'cat': 'OriginLab', 'label': '8876'}, {'cat': 'Photoshop', 'label': '8534'}, {'cat': 'CorelDRAW', 'label': '8283'}, {'cat': 'ImageMagick', 'label': '8050'}, {'cat': 'Acrobat', 'label': '7109'}, {'cat': 'PowerPoint', 'label': '5339'}, {'cat': 'jpeg2ps', 'label': '4851'}, {'cat': 'Ipe', 'labe